In [1]:
import arviz as az
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import pymc3 as pm
import xarray as xr
from scipy.special import expit as logistic

In [2]:
%config InlineBackend.figure_format = 'retina'
RANDOM_SEED = 8927
np.random.seed(RANDOM_SEED)
az.style.use("arviz-darkgrid")

In [3]:
PARTIES = {
    "chirac2": "right",
    "sarkozy": "right",
    "hollande": "left",
    "macron": "center",
}


def standardize(series):
    """Standardize a pandas series"""
    return (series - series.mean()) / series.std()

In [6]:
all_presidents = pd.read_csv(
    "../data/raw_popularity_presidents.csv", index_col=0, parse_dates=True
)
all_presidents

president sondage  samplesize        method  approve_pr  \
1978-09-28       vge  Kantar        1040  face to face        60.0   
1978-10-17       vge    Ifop         949         phone        52.0   
1978-10-28       vge  Kantar         964  face to face        59.0   
1978-11-19       vge    Ifop        1069         phone        53.0   
1978-11-24       vge  Kantar         928  face to face        62.0   
...              ...     ...         ...           ...         ...   
2020-11-27    macron    Ifop        1013      internet        41.0   
2020-11-28    macron  Kantar        1000  face to face        38.0   
2020-12-02    macron   Elabe        1000      internet        32.0   
2021-01-06    macron   Elabe        1001      internet        35.0   
2021-01-08    macron    Ifop        1028      internet        45.0   

            disapprove_pr  
1978-09-28           33.0  
1978-10-17           35.0  
1978-10-28           34.0  
1978-11-19           37.0  
1978-11-24           33.0  
...                   ...  
2020-11-27           59.0  
2020-11-28           58.0  
2020-12-02           64.0  
2021-01-06           61.0  
2021-01-08           55.0  

[1890 rows x 6 columns]

In [7]:
# restrict data to after the switch to 5-year term
d = all_presidents.loc[all_presidents.index >= pd.to_datetime("2002-05-05")]

# convert to proportions
d[["approve_pr", "disapprove_pr"]] = d[["approve_pr", "disapprove_pr"]].copy() / 100
d = d.rename(columns={"approve_pr": "p_approve", "disapprove_pr": "p_disapprove"})

# raw monthly average to get fixed time intervals
# TODO: replace by poll aggregation
d = d.groupby("president").resample("M").mean().reset_index(level=0).sort_index()

d["party"] = d.president.replace(PARTIES)

/Users/alex_andorra/opt/anaconda3/envs/elections-models/lib/python3.8/site-packages/pandas/core/frame.py:2963: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [8]:
ELECTION_FLAGS = (
    (d.index.year == 2002) & (d.index.month == 5)
    | (d.index.year == 2007) & (d.index.month == 5)
    | (d.index.year == 2012) & (d.index.month == 5)
    | (d.index.year == 2017) & (d.index.month == 5)
)
d["election_flag"] = 0
d.loc[ELECTION_FLAGS, "election_flag"] = 1

# convert to nbr of successes
d["N_approve"] = d.samplesize * d["p_approve"]
d["N_disapprove"] = d.samplesize * d["p_disapprove"]
d[["N_approve", "N_disapprove"]] = d[["N_approve", "N_disapprove"]].round().astype(int)

# compute total trials
d["N_total"] = d.N_approve + d.N_disapprove
d

president   samplesize  p_approve  p_disapprove   party  \
2002-05-31   chirac2   964.250000   0.502500      0.442500   right   
2002-06-30   chirac2   970.000000   0.505000      0.425000   right   
2002-07-31   chirac2   947.333333   0.533333      0.406667   right   
2002-08-31   chirac2  1028.000000   0.520000      0.416667   right   
2002-09-30   chirac2  1017.500000   0.525000      0.420000   right   
...              ...          ...        ...           ...     ...   
2020-09-30    macron  1000.500000   0.320000      0.625000  center   
2020-10-31    macron  1000.000000   0.373333      0.573333  center   
2020-11-30    macron  1188.000000   0.384000      0.586000  center   
2020-12-31    macron  1000.000000   0.320000      0.640000  center   
2021-01-31    macron  1014.500000   0.400000      0.580000  center   

            election_flag  N_approve  N_disapprove  N_total  
2002-05-31              1        485           427      912  
2002-06-30              0        490           412      902  
2002-07-31              0        505           385      890  
2002-08-31              0        535           428      963  
2002-09-30              0        534           427      961  
...                   ...        ...           ...      ...  
2020-09-30              0        320           625      945  
2020-10-31              0        373           573      946  
2020-11-30              0        456           696     1152  
2020-12-31              0        320           640      960  
2021-01-31              0        406           588      994  

[225 rows x 9 columns]

In [9]:
def dates_to_idx(timelist):
    """Convert datetimes to numbers in reference to a given date. Useful for posterior predictions."""

    reference_time = timelist[0]
    t = (timelist - reference_time) / np.timedelta64(1, "M")

    return np.asarray(t)

In [10]:
time = dates_to_idx(d.index)
time[:10]

array([0.        , 0.98564652, 2.00414793, 3.02264934, 4.00829586,
       5.02679726, 6.01244379, 7.03094519, 8.0494466 , 8.96938335])

In [11]:
unemp = pd.read_csv(
    "../data/predictors/chomage_national_trim.csv", sep=";", skiprows=2
).iloc[:, [0, 1]]
unemp.columns = ["date", "unemployment"]
unemp = unemp.sort_values("date")

# as timestamps variables:
unemp.index = pd.period_range(start=unemp.date.iloc[0], periods=len(unemp), freq="Q")
unemp = unemp.drop("date", axis=1)
unemp

unemployment
1975Q1           2.9
1975Q2           3.2
1975Q3           3.5
1975Q4           3.6
1976Q1           3.6
...              ...
2019Q3           8.1
2019Q4           7.8
2020Q1           7.6
2020Q2           7.0
2020Q3           8.8

[183 rows x 1 columns]

In [12]:
d = d.reset_index()

# add quarters to main dataframe:
d.index = pd.DatetimeIndex(d["index"].values).to_period("Q")
d.index.name = "quarter"

# merge with unemployment:
d = d.join(unemp).reset_index().set_index("index")
d.index.name = "month"
d["unemployment"] = d.unemployment.fillna(method="ffill")
d

quarter president   samplesize  p_approve  p_disapprove   party  \
month                                                                        
2002-05-31  2002Q2   chirac2   964.250000   0.502500      0.442500   right   
2002-06-30  2002Q2   chirac2   970.000000   0.505000      0.425000   right   
2002-07-31  2002Q3   chirac2   947.333333   0.533333      0.406667   right   
2002-08-31  2002Q3   chirac2  1028.000000   0.520000      0.416667   right   
2002-09-30  2002Q3   chirac2  1017.500000   0.525000      0.420000   right   
...            ...       ...          ...        ...           ...     ...   
2020-09-30  2020Q3    macron  1000.500000   0.320000      0.625000  center   
2020-10-31  2020Q4    macron  1000.000000   0.373333      0.573333  center   
2020-11-30  2020Q4    macron  1188.000000   0.384000      0.586000  center   
2020-12-31  2020Q4    macron  1000.000000   0.320000      0.640000  center   
2021-01-31  2021Q1    macron  1014.500000   0.400000      0.580000  center   

            election_flag  N_approve  N_disapprove  N_total  unemployment  
month                                                                      
2002-05-31              1        485           427      912           7.5  
2002-06-30              0        490           412      902           7.5  
2002-07-31              0        505           385      890           7.5  
2002-08-31              0        535           428      963           7.5  
2002-09-30              0        534           427      961           7.5  
...                   ...        ...           ...      ...           ...  
2020-09-30              0        320           625      945           8.8  
2020-10-31              0        373           573      946           8.8  
2020-11-30              0        456           696     1152           8.8  
2020-12-31              0        320           640      960           8.8  
2021-01-31              0        406           588      994           8.8  

[225 rows x 11 columns]

In [13]:
# change-points / Linzer model
# uncertainty in y (pollsters weights)
# economy: GRW

In [14]:
trace_econ = az.from_netcdf("trace_raw_econ.nc")

In [15]:
MAX_OBSERVED = len(d.index)
TIME_BEFORE_ORIGIN = 0
MAX_TIME = MAX_OBSERVED + 3  # 1 quarter out-of-sample
RANGE_OOS = MAX_TIME + TIME_BEFORE_ORIGIN

tnew = np.linspace(-TIME_BEFORE_ORIGIN, MAX_TIME, RANGE_OOS)[:, None]

In [16]:
log_unemp = np.log(d.unemployment)

# unemployment stays around last value
ppc_unemp = np.random.normal(
    loc=d.unemployment.iloc[-1],
    scale=d.unemployment.std(),
    size=(MAX_TIME - MAX_OBSERVED) // 3,
)
# data only observed quarterly, so need to forward-fill
ppc_unemp = np.repeat(ppc_unemp, repeats=3)

# log data and scale
stdz_log_ppc_unemp = (np.log(ppc_unemp) - log_unemp.mean()) / log_unemp.std()

# add noise around values
oos_unemp = stdz_log_ppc_unemp + np.random.normal(
    loc=trace_econ.posterior["u_diff"].mean(),
    scale=trace_econ.posterior["u_diff"].std(),
    size=MAX_TIME - MAX_OBSERVED,
)
oos_unemp

array([-0.26808107, -0.04908828,  0.08836651])

In [17]:
# unemployment jumps to 10%
ppc_unemp_10 = np.random.normal(
    loc=10.0, scale=d.unemployment.std(), size=(MAX_TIME - MAX_OBSERVED) // 3
)
# data only observed quarterly, so need to forward-fill
ppc_unemp_10 = np.repeat(ppc_unemp_10, repeats=3)

# log data and scale
stdz_log_ppc_unemp_10 = (np.log(ppc_unemp_10) - log_unemp.mean()) / log_unemp.std()

# add noise around values
oos_unemp_10 = stdz_log_ppc_unemp_10 + np.random.normal(
    loc=trace_econ.posterior["u_diff"].mean(),
    scale=trace_econ.posterior["u_diff"].std(),
    size=MAX_TIME - MAX_OBSERVED,
)
oos_unemp_10

array([0.99572503, 1.35125148, 0.92024266])

In [18]:
# unemployment drops to 5%
ppc_unemp_5 = np.random.normal(
    loc=5.0, scale=d.unemployment.std(), size=(MAX_TIME - MAX_OBSERVED) // 3
)
# data only observed quarterly, so need to forward-fill
ppc_unemp_5 = np.repeat(ppc_unemp_5, repeats=3)

# log data and scale
stdz_log_ppc_unemp_5 = (np.log(ppc_unemp_5) - log_unemp.mean()) / log_unemp.std()

# add noise around values
oos_unemp_5 = stdz_log_ppc_unemp_5 + np.random.normal(
    loc=trace_econ.posterior["u_diff"].mean(),
    scale=trace_econ.posterior["u_diff"].std(),
    size=MAX_TIME - MAX_OBSERVED,
)
oos_unemp_5

array([-4.76412966, -4.81001921, -4.81604108])

In [19]:
COORDS = {"timesteps": d.index}

with pm.Model(coords=COORDS) as econ_latent_gp:
    # intercept on logit scale
    baseline = pm.Normal("baseline", -0.7, 0.5)

    # honeymoon slope
    honeymoon = pm.Normal("honeymoon", -0.5, 0.3)

    # log unemployment slope
    log_unemp_effect = pm.Normal("log_unemp_effect", 0.0, 0.2)

    # long term trend
    amplitude_trend = pm.HalfNormal("amplitude_trend", 1.0)
    ls_trend = pm.Gamma("ls_trend", alpha=5, beta=2)
    cov_trend = amplitude_trend ** 2 * pm.gp.cov.Matern52(1, ls_trend)

    # instantiate gp
    gp = pm.gp.Latent(cov_func=cov_trend)
    # evaluate GP at time points
    f_time = gp.prior("f_time", X=time[:, None])

    # data
    election_flag = pm.Data("election_flag", d.election_flag.values, dims="timesteps")
    stdz_log_unemployment = pm.Data(
        "stdz_log_unemployment",
        standardize(np.log(d.unemployment)).values,
        dims="timesteps",
    )
    # unemployment data is uncertain
    # sd = 0.1 says uncertainty on point expected btw 20% of data std 95% of time
    u_diff = pm.Normal("u_diff", mu=0.0, sigma=0.1, dims="timesteps")
    u_uncert = stdz_log_unemployment + u_diff

    # overdispersion parameter
    theta = pm.Exponential("theta_offset", 1.0) + 10.0

    p = pm.Deterministic(
        "p",
        pm.math.invlogit(
            baseline + f_time + honeymoon * election_flag + log_unemp_effect * u_uncert
        ),
        dims="timesteps",
    )

    y = pm.BetaBinomial(
        "y",
        alpha=p * theta,
        beta=(1.0 - p) * theta,
        n=d.N_total,
        observed=d.N_approve,
        dims="timesteps",
    )

In [20]:
PREDICTION_COORDS = {
    "timesteps": pd.date_range(
        start=COORDS["timesteps"][0],
        end=COORDS["timesteps"][-1] + pd.DateOffset(months=3),
        freq="M",
    )
}

with econ_latent_gp:
    pm.set_data(
        {
            "election_flag": np.concatenate(
                (
                    d.election_flag.values,
                    np.zeros(MAX_TIME - MAX_OBSERVED, dtype=int),
                )
            ),
            "stdz_log_unemployment": np.concatenate(
                (standardize(log_unemp).values, oos_unemp)
            ),
        }
    )
    f_time_new = gp.conditional("f_time_new", Xnew=tnew)

    ppc = pm.sample_posterior_predictive(
        trace_econ.posterior,
        samples=1000,
        var_names=["baseline", "f_time_new", "honeymoon", "log_unemp_effect"],
    )

    az.from_pymc3_predictions(
        ppc,
        idata_orig=trace_econ,
        inplace=True,
        coords=PREDICTION_COORDS,
        dims={"f_time_new": ["timesteps"]},
    )

trace_econ

/Users/alex_andorra/opt/anaconda3/envs/elections-models/lib/python3.8/site-packages/pymc3/sampling.py:1707: UserWarning: samples parameter is smaller than nchains times ndraws, some draws and/or chains may not be represented in the returned posterior predictive sample
  warnings.warn(


Inference data with groups:
	> posterior
	> predictions
	> log_likelihood
	> sample_stats
	> observed_data
	> constant_data
	> predictions_constant_data

In [21]:
pp_prop = logistic(
    trace_econ.predictions["baseline"]
    + trace_econ.predictions["f_time_new"]
    + trace_econ.predictions["honeymoon"]
    * trace_econ.predictions_constant_data["election_flag"]
    + trace_econ.predictions["log_unemp_effect"]
    * trace_econ.predictions_constant_data["stdz_log_unemployment"]
)

In [22]:
pp_prop_10 = logistic(
    trace_econ.predictions["baseline"]
    + trace_econ.predictions["f_time_new"]
    + trace_econ.predictions["honeymoon"]
    * trace_econ.predictions_constant_data["election_flag"]
    + trace_econ.predictions["log_unemp_effect"]
    * xr.DataArray(
        np.concatenate((standardize(log_unemp).values, oos_unemp_10)),
        dims=["timesteps"],
        coords=PREDICTION_COORDS,
    )
)

In [23]:
pp_prop_5 = logistic(
    trace_econ.predictions["baseline"]
    + trace_econ.predictions["f_time_new"]
    + trace_econ.predictions["honeymoon"]
    * trace_econ.predictions_constant_data["election_flag"]
    + trace_econ.predictions["log_unemp_effect"]
    * xr.DataArray(
        np.concatenate((standardize(log_unemp).values, oos_unemp_5)),
        dims=["timesteps"],
        coords=PREDICTION_COORDS,
    )
)

In [47]:
from typing import Dict, List, Tuple

from bokeh.layouts import column
from bokeh.models import (
    Band,
    ColumnDataSource,
    DatetimeTickFormatter,
    GeoJSONDataSource,
    HoverTool,
    LabelSet,
    NumeralTickFormatter,
    Select,
    Span,
    Title,
)
from bokeh.palettes import cividis, inferno, viridis
from bokeh.plotting import figure, output_file, output_notebook, show

# from bokeh.io import output_file

In [48]:
# output_notebook()
output_file("../../pollsposition_website/templates/gp-plot.html")

In [26]:
def get_data_source(
    trace: az.InferenceData, post_pred_samples: az.InferenceData
) -> pd.DataFrame:
    source_df = (
        post_pred_samples.stack(sample=("chain", "draw"))
        .to_pandas()
        .droplevel(0, axis=1)
    )
    source_df.columns = source_df.columns.astype(str)

    source_df["baseline"] = logistic(trace.predictions["baseline"]).mean().data
    source_df["baseline_lower"] = (
        logistic(az.hdi(trace.predictions)["baseline"]).sel(hdi="lower").data
    )
    source_df["baseline_upper"] = (
        logistic(az.hdi(trace.predictions)["baseline"]).sel(hdi="higher").data
    )

    source_df["median_app"] = post_pred_samples.median(dim=("chain", "draw")).data
    source_df["median_low"] = (
        az.hdi(post_pred_samples, hdi_prob=0.75).sel(hdi="lower")["x"].data
    )
    source_df["median_high"] = (
        az.hdi(post_pred_samples, hdi_prob=0.75).sel(hdi="higher")["x"].data
    )

    return source_df

In [27]:
def samples_subset(data_source: pd.DataFrame, frac: float = 0.1) -> Dict[str, List]:

    sub_source = data_source.filter(regex="\d", axis="columns").sample(
        frac=frac, replace=True, axis="columns"
    )

    dates = []
    draws = []
    for draw in sub_source.columns:
        dates.append(sub_source.index.values)
        draws.append(sub_source[draw].values)

    return {"dates": dates, "draws": draws}

In [28]:
source_annotations = ColumnDataSource(
    data=dict(
        dates=[
            pd.to_datetime("2002-05-14"),
            pd.to_datetime("2007-05-16"),
            pd.to_datetime("2012-05-11"),
            pd.to_datetime("2017-05-17"),
            pd.to_datetime("2020-03-17"),
            pd.to_datetime("2002-10-24"),
        ],
        ys=[0.95, 0.95, 0.95, 0.95, 0.95, 0.32],
        events=[
            "Switch to 5-year term",
            "Sarkozy elected",
            "Hollande elected",
            "Macron elected",
            "1st Covid Cases",
            "Historical approval mean",
        ],
    )
)

In [29]:
raw_polls = all_presidents.loc[all_presidents.index >= pd.to_datetime("2002-05-05")]

# convert to proportions
raw_polls[["approve_pr", "disapprove_pr"]] = (
    raw_polls[["approve_pr", "disapprove_pr"]].copy() / 100
)
raw_polls = raw_polls.rename(
    columns={"approve_pr": "p_approve", "disapprove_pr": "p_disapprove"}
)

/Users/alex_andorra/opt/anaconda3/envs/elections-models/lib/python3.8/site-packages/pandas/core/frame.py:2963: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [52]:
def make_plot(
    subtitle: str,
    palette,
    random_draws: Dict[str, List],
    data_source: pd.DataFrame,
    post_pred_samples: az.InferenceData,
):
    CDS = ColumnDataSource(data_source)

    p = figure(
        plot_width=1200,
        plot_height=425,
        sizing_mode="scale_both",
        background_fill_color="#f2f2f2",
        border_fill_color="#f2f2f2",
        x_axis_type="datetime",
        title="Evolution of French presidents' popularity over time",
        x_range=(
            pd.to_datetime("2012-01-01"),
            PREDICTION_COORDS["timesteps"][-1] + pd.DateOffset(months=3),
        ),
        y_range=(0, 1),
        toolbar_location="above",
        tools="xpan, box_zoom, xwheel_zoom, crosshair, reset, undo, save",
    )
    p.xaxis[0].formatter = DatetimeTickFormatter(months="%b %Y", days="%d/%m")
    p.yaxis[0].formatter = NumeralTickFormatter(format="00%")
    p.add_layout(
        Title(
            text=f"One quarter out-of-sample, if unemployment {subtitle}",
            align="center",
            text_font_style="italic",
            text_font_size="1.2em",
        ),
        "above",
    )
    p.title.text_font_size = "1.6em"
    p.title.align = "center"
    p.grid.grid_line_alpha = 0.5
    p.xaxis.axis_label = "Date"
    p.yaxis.axis_label = "% popularity"

    p.multi_line(
        xs=random_draws["dates"],
        ys=random_draws["draws"],
        color=palette[4],
        legend_label="Random samples",
    )
    p.patch(
        np.concatenate((data_source.index.values, data_source.index.values[::-1])),
        np.concatenate(
            (
                az.hdi(post_pred_samples)["x"][:, 0],
                az.hdi(post_pred_samples)["x"][:, 1][::-1],
            )
        ),
        color=palette[3],
        line_alpha=0.4,
        fill_alpha=0.4,
        legend_label="94% HDI",
    )
    hdi = p.patch(
        np.concatenate((data_source.index.values, data_source.index.values[::-1])),
        np.concatenate(
            (
                az.hdi(post_pred_samples, hdi_prob=0.75)["x"][:, 0],
                az.hdi(post_pred_samples, hdi_prob=0.75)["x"][:, 1][::-1],
            )
        ),
        color=palette[2],
        line_alpha=0,
        fill_alpha=0.5,
        legend_label="75% HDI",
    )
    p.patch(
        np.concatenate((data_source.index.values, data_source.index.values[::-1])),
        np.concatenate(
            (
                az.hdi(post_pred_samples, hdi_prob=0.5)["x"][:, 0],
                az.hdi(post_pred_samples, hdi_prob=0.5)["x"][:, 1][::-1],
            )
        ),
        color=palette[1],
        line_alpha=0,
        fill_alpha=0.6,
        legend_label="50% HDI",
    )
    median_line = p.line(
        "timesteps",
        "median_app",
        color=palette[0],
        line_width=2,
        legend_label="Median",
        source=CDS,
    )
    p.scatter(
        raw_polls.index.values,
        raw_polls.p_approve.values,
        size=6,
        color=palette[5],
        legend_label="Observed polls",
        alpha=0.7,
    )

    labels = LabelSet(
        x="dates",
        y="ys",
        text="events",
        level="glyph",
        text_color="gray",
        text_font_style="italic",
        text_font_size="1em",
        text_align="center",
        source=source_annotations,
    )
    vline_0 = Span(
        location=source_annotations.data["dates"][0],
        dimension="height",
        line_color="gray",
        line_dash="dashed",
        line_width=1.5,
    )
    vline_1 = Span(
        location=source_annotations.data["dates"][1],
        dimension="height",
        line_color="gray",
        line_dash="dashed",
        line_width=1.5,
    )
    vline_2 = Span(
        location=source_annotations.data["dates"][2],
        dimension="height",
        line_color="gray",
        line_dash="dashed",
        line_width=1.5,
    )
    vline_3 = Span(
        location=source_annotations.data["dates"][3],
        dimension="height",
        line_color="gray",
        line_dash="dashed",
        line_width=1.5,
    )
    vline_4 = Span(
        location=source_annotations.data["dates"][4],
        dimension="height",
        line_color="gray",
        line_dash="dashed",
        line_width=1.5,
    )

    fifty_line = Span(
        location=0.5,
        dimension="width",
        line_color="gray",
        line_dash="dotted",
        line_width=1.5,
    )
    hist_band = Band(
        base="timesteps",
        lower="baseline_lower",
        upper="baseline_upper",
        source=CDS,
        fill_color="gray",
        fill_alpha=0.2,
    )
    hist_avg_line = Span(
        location=CDS.data["baseline"][0],
        dimension="width",
        line_color="gray",
        line_dash="dashdot",
        line_width=2,
    )

    p.renderers.extend(
        [
            labels,
            vline_0,
            vline_1,
            vline_2,
            vline_3,
            vline_4,
            fifty_line,
            hist_band,
            hist_avg_line,
        ]
    )

    p.legend.click_policy = "hide"
    p.legend.location = "top_left"
    p.legend.orientation = "horizontal"
    p.legend.background_fill_color = "#f2f2f2"
    p.legend.background_fill_alpha = 0.6

    # Add the HoverTool to the figure
    TOOLTIPS = [
        ("Median app.", "@median_app{00%} in @timesteps{%b %Y}"),
        ("75% chance btw", "@median_low{00%} and @median_high{00%}"),
        ("Historic. avg. btw", "@baseline_lower{00%} and @baseline_upper{00%}"),
    ]
    p.add_tools(
        HoverTool(
            tooltips=TOOLTIPS,
            formatters={"@timesteps": "datetime"},
            mode="vline",
            renderers=[median_line],
        )
    )

    return p

In [31]:
source_df1 = get_data_source(trace_econ, pp_prop)
source_df2 = get_data_source(trace_econ, pp_prop_5)
source_df3 = get_data_source(trace_econ, pp_prop_10)

In [32]:
random_draws1 = samples_subset(source_df1)
random_draws2 = samples_subset(source_df2)
random_draws3 = samples_subset(source_df3)

In [53]:
p1 = make_plot(
    subtitle=f"stays at {d.unemployment.iloc[-1]}%",
    palette=viridis(6),
    random_draws=random_draws1,
    data_source=source_df1,
    post_pred_samples=pp_prop,
)
p2 = make_plot(
    subtitle="drops to 5%",
    palette=cividis(6),
    random_draws=random_draws2,
    data_source=source_df2,
    post_pred_samples=pp_prop_5,
)
p3 = make_plot(
    subtitle="increases to 10%",
    palette=inferno(6),
    random_draws=random_draws3,
    data_source=source_df3,
    post_pred_samples=pp_prop_10,
)

p2.title.text = None
p3.title.text = None
p2.x_range = p1.x_range
p3.x_range = p1.x_range

show(column(p1, p2, p3))